## Install dependencies

In [1]:
%pip install -r requirements.txt

Note: you may need to restart the kernel to use updated packages.


ERROR: Could not open requirements file: [Errno 2] No such file or directory: 'requirements.txt'

[notice] A new release of pip is available: 24.1 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
import pandas as pd
from pymongo import MongoClient
from pyspark.sql import SparkSession
import os
from pyspark.sql.functions import year
import time

## Insert data into Mongodb

The datasets are currently files in .csv format, we have to import them into Mondodb

In [3]:
'''Insert ratings.csv into MongoDB'''
# load csv file into pandas DataFrame first
df = pd.read_csv("dataset/ml-latest-small/ratings.csv")

# =specify Mongodb client, database and collection
client = MongoClient('mongodb://localhost:27017/')
db = client["test"]
collection = db["ratings"]

# convert DataFrame to a list of dictionaries (one for each row)
data = df.to_dict(orient="records")

# insert data into MongoDB
collection.insert_many(data)

InsertManyResult([ObjectId('6745127901820ef6606ca32c'), ObjectId('6745127901820ef6606ca32d'), ObjectId('6745127901820ef6606ca32e'), ObjectId('6745127901820ef6606ca32f'), ObjectId('6745127901820ef6606ca330'), ObjectId('6745127901820ef6606ca331'), ObjectId('6745127901820ef6606ca332'), ObjectId('6745127901820ef6606ca333'), ObjectId('6745127901820ef6606ca334'), ObjectId('6745127901820ef6606ca335'), ObjectId('6745127901820ef6606ca336'), ObjectId('6745127901820ef6606ca337'), ObjectId('6745127901820ef6606ca338'), ObjectId('6745127901820ef6606ca339'), ObjectId('6745127901820ef6606ca33a'), ObjectId('6745127901820ef6606ca33b'), ObjectId('6745127901820ef6606ca33c'), ObjectId('6745127901820ef6606ca33d'), ObjectId('6745127901820ef6606ca33e'), ObjectId('6745127901820ef6606ca33f'), ObjectId('6745127901820ef6606ca340'), ObjectId('6745127901820ef6606ca341'), ObjectId('6745127901820ef6606ca342'), ObjectId('6745127901820ef6606ca343'), ObjectId('6745127901820ef6606ca344'), ObjectId('6745127901820ef6606ca3

In [4]:
'''Insert movies.csv into MongoDB'''
file_path = os.path.join('dataset', 'ml-latest-small', 'movies.csv')

df = pd.read_csv(file_path)

client = MongoClient('mongodb://localhost:27017/')
db = client["test"]
collection = db["movies"]

data = df.to_dict(orient="records")
collection.insert_many(data)

InsertManyResult([ObjectId('6745127b01820ef6606e2d11'), ObjectId('6745127b01820ef6606e2d12'), ObjectId('6745127b01820ef6606e2d13'), ObjectId('6745127b01820ef6606e2d14'), ObjectId('6745127b01820ef6606e2d15'), ObjectId('6745127b01820ef6606e2d16'), ObjectId('6745127b01820ef6606e2d17'), ObjectId('6745127b01820ef6606e2d18'), ObjectId('6745127b01820ef6606e2d19'), ObjectId('6745127b01820ef6606e2d1a'), ObjectId('6745127b01820ef6606e2d1b'), ObjectId('6745127b01820ef6606e2d1c'), ObjectId('6745127b01820ef6606e2d1d'), ObjectId('6745127b01820ef6606e2d1e'), ObjectId('6745127b01820ef6606e2d1f'), ObjectId('6745127b01820ef6606e2d20'), ObjectId('6745127b01820ef6606e2d21'), ObjectId('6745127b01820ef6606e2d22'), ObjectId('6745127b01820ef6606e2d23'), ObjectId('6745127b01820ef6606e2d24'), ObjectId('6745127b01820ef6606e2d25'), ObjectId('6745127b01820ef6606e2d26'), ObjectId('6745127b01820ef6606e2d27'), ObjectId('6745127b01820ef6606e2d28'), ObjectId('6745127b01820ef6606e2d29'), ObjectId('6745127b01820ef6606e2d

## Use Apache Spark for parallel data processing

### Initial a Spark Session

In [5]:
# spark = SparkSession.builder \
#     .appName("Big-Data-Demo") \
#     .master("local[*]") \
#     .config("spark.jars.packages", "org.mongodb.spark:mongo-spark-connector_2.12:3.0.1") \
#     .config("spark.mongodb.read.connection.uri", "mongodb://127.0.0.1:27017/")  \
#     .getOrCreate() \
    
spark = SparkSession.builder \
    .appName("Big-Data-Demo") \
    .master("local[*]") \
    .config("spark.jars.packages", "org.mongodb.spark:mongo-spark-connector_2.12:3.0.1") \
    .config("spark.mongodb.read.connection.uri", "mongodb://127.0.0.1:27017/") \
    .getOrCreate() \

print(f"----------spark version: {spark.version}------------")

----------spark version: 3.5.3------------


### Load data from MongoDB

#### Load all data from a collection

In [6]:
# load all data from MongoDB
df_ratings = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/")\
    .option("database", "test")\
    .option("collection", "ratings")\
    .load()    

df_movies = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/test.movies")\
    .option("database", "test")\
    .option("collection", "movies")\
    .load()   

# Show the loaded data
print(f"Original Rating Data:")
print(df_ratings.show())
print(f"Original Movie Data:")
print( df_movies.show())

Original Rating Data:
+--------------------+-------+------+---------+------+
|                 _id|movieId|rating|timestamp|userId|
+--------------------+-------+------+---------+------+
|{6743f02df2b2062a...|      1|   4.0|964982703|     1|
|{6743f02df2b2062a...|      3|   4.0|964981247|     1|
|{6743f02df2b2062a...|      6|   4.0|964982224|     1|
|{6743f02df2b2062a...|     47|   5.0|964983815|     1|
|{6743f02df2b2062a...|     50|   5.0|964982931|     1|
|{6743f02df2b2062a...|     70|   3.0|964982400|     1|
|{6743f02df2b2062a...|    101|   5.0|964980868|     1|
|{6743f02df2b2062a...|    110|   4.0|964982176|     1|
|{6743f02df2b2062a...|    151|   5.0|964984041|     1|
|{6743f02df2b2062a...|    157|   5.0|964984100|     1|
|{6743f02df2b2062a...|    163|   5.0|964983650|     1|
|{6743f02df2b2062a...|    216|   5.0|964981208|     1|
|{6743f02df2b2062a...|    223|   3.0|964980985|     1|
|{6743f02df2b2062a...|    231|   5.0|964981179|     1|
|{6743f02df2b2062a...|    235|   4.0|964980

#### Make query to the database

In [7]:
# sol 1: failed, maybe because of the version of the spark
query = '{"rating": {"$gt": 4}}'
print(f"Query sent to MongoDB: {query}")

# Load filtered data
df_ratings_filtered = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/")\
    .option("database", "test")\
    .option("collection", "ratings")\
    .option("query", query)\
    .load()

# Show filtered data
print("Filtered Data (movies with rating > 4):")
df_ratings_filtered.show()
query = '{"rating": {"$gt": 4}}'

Query sent to MongoDB: {"rating": {"$gt": 4}}
Filtered Data (movies with rating > 4):
+--------------------+-------+------+---------+------+
|                 _id|movieId|rating|timestamp|userId|
+--------------------+-------+------+---------+------+
|{6743f02df2b2062a...|      1|   4.0|964982703|     1|
|{6743f02df2b2062a...|      3|   4.0|964981247|     1|
|{6743f02df2b2062a...|      6|   4.0|964982224|     1|
|{6743f02df2b2062a...|     47|   5.0|964983815|     1|
|{6743f02df2b2062a...|     50|   5.0|964982931|     1|
|{6743f02df2b2062a...|     70|   3.0|964982400|     1|
|{6743f02df2b2062a...|    101|   5.0|964980868|     1|
|{6743f02df2b2062a...|    110|   4.0|964982176|     1|
|{6743f02df2b2062a...|    151|   5.0|964984041|     1|
|{6743f02df2b2062a...|    157|   5.0|964984100|     1|
|{6743f02df2b2062a...|    163|   5.0|964983650|     1|
|{6743f02df2b2062a...|    216|   5.0|964981208|     1|
|{6743f02df2b2062a...|    223|   3.0|964980985|     1|
|{6743f02df2b2062a...|    231|   5

In [8]:
# set format as "mongo" instead of "mongodb", set uri
start_time = time.time()
df_ratings_filtered = spark.read.format("mongo").option("uri", "mongodb://127.0.0.1:27017/") \
                 .option("database", "test") \
                 .option("collection", "ratings") \
                 .load()

df_ratings_filtered.filter(df_ratings_filtered['rating'] > 4)
end_time = time.time()
df_ratings_filtered.head()
print(f"Execution time: {end_time - start_time} seconds")

Execution time: 0.21632814407348633 seconds


In [9]:
# sol 2: return cursors points to rows in the collection
start_time = time.time()
client = MongoClient('mongodb://localhost:27017/')
db = client["test"]
collection = db["ratings"]

query = {"rating": {"$gt": 4}}  # Find documents where age > 25
cursors = collection.find(query)

# for doc in results:
#     print(doc)

stop_time1 = time.time()

filtered_df = pd.DataFrame(list(cursors))
stop_time = time.time()
print(filtered_df.head())
print(f"Time taken to fetch data from MongoDB: {stop_time1 - start_time}")
print(f"Total time taken: {stop_time - start_time}")
# cursors = list(cursors)
# print(cursors[0]['userId', 'movieId', 'rating', 'timestamp'])

# filtered_df = spark.createDataFrame(list(cursors))
# filtered_df.show()

                        _id  userId  movieId  rating  timestamp
0  6743f02df2b2062a22ecadae       1       47     5.0  964983815
1  6743f02df2b2062a22ecadaf       1       50     5.0  964982931
2  6743f02df2b2062a22ecadb1       1      101     5.0  964980868
3  6743f02df2b2062a22ecadb3       1      151     5.0  964984041
4  6743f02df2b2062a22ecadb4       1      157     5.0  964984100
Time taken to fetch data from MongoDB: 0.0040130615234375
Total time taken: 0.9110825061798096


In [10]:
# sol 3: get the dataframe, then filter it using pandas => worse than using MongoDB query
start_time = time.time()
df_ratings = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/test.ratings")\
    .load()

df_ratings_pd = df_ratings.toPandas()
df_ratings_pd = df_ratings_pd[df_ratings_pd['rating'] > 4]

df_ratings_pd.head()
stop_time = time.time()
print(f"Time taken: {stop_time - start_time}")

Time taken: 19.08342432975769


### Spark's dataframe operations

In [11]:
# df_movies.show()
# df_ratings.show()

joined_df = df_movies.join(df_ratings, on="movieId", how="right")
print(f"movies_ratings_df:")
# print(joined_df.columns)
# print(joined_df.select("timestamp").show())
# print(type(joined_df))
joined_df.show()

movies_ratings_df:
+-------+--------------------+--------------------+--------------------+--------------------+------+---------+------+
|movieId|                 _id|              genres|               title|                 _id|rating|timestamp|userId|
+-------+--------------------+--------------------+--------------------+--------------------+------+---------+------+
|      1|{6743f02df2b2062a...|Adventure|Animati...|    Toy Story (1995)|{6743f02df2b2062a...|   4.0|964982703|     1|
|      1|{674450be3c85934c...|Adventure|Animati...|    Toy Story (1995)|{6743f02df2b2062a...|   4.0|964982703|     1|
|      1|{67450b9460d4f003...|Adventure|Animati...|    Toy Story (1995)|{6743f02df2b2062a...|   4.0|964982703|     1|
|      1|{6745127b01820ef6...|Adventure|Animati...|    Toy Story (1995)|{6743f02df2b2062a...|   4.0|964982703|     1|
|      3|{6743f02df2b2062a...|      Comedy|Romance|Grumpier Old Men ...|{6743f02df2b2062a...|   4.0|964981247|     1|
|      3|{674450be3c85934c...|      C

### Create a new column named "Year"

In [12]:
from pyspark.sql.functions import substring
from pyspark.sql.functions import col

joined_df = joined_df.withColumn("year", substring("title", -5, 4))
joined_df = joined_df.filter(col("year").rlike("^[12]"))
joined_df = joined_df.withColumn("year", col("year").cast("int"))

joined_df.show()
# joined_df.select("year").distinct().show()

+-------+--------------------+--------------------+--------------------+--------------------+------+----------+------+----+
|movieId|                 _id|              genres|               title|                 _id|rating| timestamp|userId|year|
+-------+--------------------+--------------------+--------------------+--------------------+------+----------+------+----+
|   1580|{6745127b01820ef6...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6743f02df2b2062a...|   3.0| 964981125|     1|1997|
|   1580|{67450b9460d4f003...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6743f02df2b2062a...|   3.0| 964981125|     1|1997|
|   1580|{674450be3c85934c...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6743f02df2b2062a...|   3.0| 964981125|     1|1997|
|   1580|{6743f02df2b2062a...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6743f02df2b2062a...|   3.0| 964981125|     1|1997|
|   2366|{6745127b01820ef6...|Action|Adventure|...|    King Kong (1933)|{6743f02df2b2062a...|   4.0| 964982462|     1|1933|
|   2366

## Train a movie recommender model

### Linear Regression Model

In [13]:
# recommender = RecommendationEngine(joined_df)

In [14]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.regression import LinearRegression
from pyspark.ml.evaluation import RegressionEvaluator

In [15]:
feature_assembler = VectorAssembler(inputCols=["userId", "movieId"], outputCol="features")
assembled_df = feature_assembler.transform(joined_df)
(training_data, test_data) = assembled_df.randomSplit([0.8, 0.2])

model = LinearRegression(featuresCol="features", labelCol="rating", predictionCol="prediction")
lr_model = model.fit(training_data)

In [16]:
# make predictions
predictions = lr_model.transform(test_data)

# show predictions
predictions.select("features", "rating", "prediction").show()

# evaluate the model using R2 and RMSE
evaluator = RegressionEvaluator(labelCol="rating", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print(f"Root Mean Squared Error (RMSE): {rmse}")

evaluator.setMetricName("r2")
r2 = evaluator.evaluate(predictions)
print(f"R2: {r2}")

+------------+------+------------------+
|    features|rating|        prediction|
+------------+------+------------------+
| [19.0,12.0]|   1.0|3.5889894264465667|
| [44.0,12.0]|   1.0|  3.58205064574231|
|[276.0,12.0]|   4.0|3.5176587608068086|
|[571.0,12.0]|   1.0|3.4357811484965803|
| [44.0,12.0]|   1.0|  3.58205064574231|
|[151.0,12.0]|   3.0|3.5523526643280916|
|[276.0,12.0]|   4.0|3.5176587608068086|
|[524.0,12.0]|   1.0| 3.448826056220583|
| [19.0,12.0]|   1.0|3.5889894264465667|
|[217.0,12.0]|   3.0|3.5340342832688543|
|[274.0,12.0]|   3.5| 3.518213863263149|
|[524.0,12.0]|   1.0| 3.448826056220583|
|[599.0,12.0]|   1.5| 3.428009714107813|
|[276.0,12.0]|   4.0|3.5176587608068086|
|[288.0,12.0]|   2.0|3.5143281460687654|
|[571.0,12.0]|   1.0|3.4357811484965803|
|[217.0,12.0]|   3.0|3.5340342832688543|
|[288.0,12.0]|   2.0|3.5143281460687654|
|[294.0,12.0]|   1.0| 3.512662838699744|
|[350.0,12.0]|   3.0| 3.497119969922209|
+------------+------+------------------+
only showing top

### ALS

In [17]:
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.recommendation import ALS
from pyspark.sql import Row

ratings = joined_df.select("userId", "movieId", "rating")
(training, test) = ratings.randomSplit([0.8, 0.2])

# set cold start strategy to 'drop' to ensure we don't get NaN evaluation metrics
als = ALS(maxIter=5, regParam=0.01, userCol="userId", itemCol="movieId", ratingCol="rating",
          coldStartStrategy="drop")
model = als.fit(training)

# evaluate
predictions = model.transform(test)
evaluator = RegressionEvaluator(metricName="rmse", labelCol="rating",
                                predictionCol="prediction")
rmse = evaluator.evaluate(predictions)
print("Root-mean-square error = " + str(rmse))

# top 10 movie recommendations for each user
userRecs = model.recommendForAllUsers(10)
# top 10 user recommendations for each movie
movieRecs = model.recommendForAllItems(10)

# top 10 movie recommendations for a specified set of users
users = ratings.select(als.getUserCol()).distinct().limit(3)
userSubsetRecs = model.recommendForUserSubset(users, 10)

# top 10 user recommendations for a specified set of movies
movies = ratings.select(als.getItemCol()).distinct().limit(3)
movieSubSetRecs = model.recommendForItemSubset(movies, 10)

Root-mean-square error = 0.546270888146419


In [18]:
print(userRecs.show())

+------+--------------------+
|userId|     recommendations|
+------+--------------------+
|     1|[{3925, 6.7853904...|
|     2|[{74754, 7.789781...|
|     3|[{48322, 6.951864...|
|     4|[{34338, 7.271497...|
|     5|[{5034, 6.932786}...|
|     6|[{971, 7.036011},...|
|     7|[{4678, 9.650388}...|
|     8|[{5055, 7.2378206...|
|     9|[{106100, 7.42635...|
|    10|[{2693, 8.148736}...|
|    11|[{3200, 6.935401}...|
|    12|[{26258, 8.614412...|
|    13|[{2148, 7.473914}...|
|    14|[{2906, 11.770087...|
|    15|[{1734, 7.8901587...|
|    16|[{3925, 5.546985}...|
|    17|[{1658, 6.442111}...|
|    18|[{3200, 5.1955605...|
|    19|[{5666, 5.1309776...|
|    20|[{179819, 7.15204...|
+------+--------------------+
only showing top 20 rows

None


In [19]:
userSubsetRecs.show()
users.show()

+------+--------------------+
|userId|     recommendations|
+------+--------------------+
|   463|[{79224, 7.039547...|
|   496|[{34338, 9.542832...|
|   148|[{4450, 7.3070965...|
+------+--------------------+

+------+
|userId|
+------+
|   463|
|   496|
|   148|
+------+



In [20]:
movieSubSetRecs.show()

+-------+--------------------+
|movieId|     recommendations|
+-------+--------------------+
|   1580|[{569, 5.2485666}...|
|   3175|[{258, 6.324589},...|
|   2366|[{494, 7.989951},...|
+-------+--------------------+

